# Routing and Connections

PhotonForge makes it easy to place and connect components to build complex layouts.
Components are placed through references (see our [getting started](../getting_started.rst) page for the basic concepts used in PhotonForge) and those are connected by ports.

To demonstrate routing and connections, let us first create a few components using the 
[basic technology](../_autosummary/photonforge.basic_technology.rst) as our default [technology](Technology.ipynb).

In [1]:
import photonforge as pf

tech = pf.basic_technology()
pf.config.default_technology = tech

We also set a few default arguments for our paramteric components:

In [2]:
pf.config.default_kwargs = {
    "port_spec": "Strip",
    "radius": 5,
    "euler_fraction": 0.5,
}

We use the [parametric library](Parametric_Component_Library.ipynb) of components to create a [coupler](../_autosummary/photonforge.parametric.s_bend_coupler.rst) and a [spiral](../_autosummary/photonforge.parametric.rectangular_spiral.rst).
Note that the length of the S bends are automatically calculated based on the desired offset and default radius.

In [3]:
coupler = pf.parametric.s_bend_coupler(
    s_bend_offset=1.5,
    coupling_distance=0.6
)
coupler

In [4]:
spiral = pf.parametric.rectangular_spiral(turns=8)
spiral

We create our main component and start by adding a reference to the coupler.

In [5]:
component = pf.Component("MAIN")
coupler_ref1 = component.add_reference(coupler)
component

## Connections

We also want to add a reference to the spiral, but we want it connected to the coupler we just added.
For that we can use the reference's [connect](../_autosummary/photonforge.Reference.rst#photonforge.Reference.connect) method, which takes care of any translation, rotations, or reflection required to connect the desired ports.

In this case, we connect port P0 from the spiral reference to port P3 of the coupler reference. Note that we're using the reference's ports, not the original component's, because we have to take into account any transformations the references already have.

In [6]:
spiral_ref = component.add_reference(spiral)
spiral_ref.connect("P0", coupler_ref1["P3"])
component

We can see that the spiral reference has been translated to connect to the coupler at the appropriate port.
The reference origin can be inspected to reveal the translation:

In [7]:
spiral_ref.origin

array([10.536,  3.6  ])

## Routing

We want the second coupler to be aligned to the first, so we won't the placing it by connecting to the second port of the spiral reference.
Instead, we use the reference alignment coordinates to position it:

In [8]:
coupler_ref2 = component.add_reference(coupler)
coupler_ref2.x_min = spiral_ref.x_max + 5
coupler_ref2.y_mid = coupler_ref1.y_mid
component

The connection between the spiral and the second coupler references can be built with the help of the [route](../_autosummary/photonforge.parametric.route.rst) parametric component.
It generates a waveguide connection between 2 ports and it accepts a number of parameters for customization.
Internally, it uses other parametric components to build the path, namely, [straight](../_autosummary/photonforge.parametric.straight.rst), [bend](../_autosummary/photonforge.parametric.bend.rst), and [s_bend](../_autosummary/photonforge.parametric.s_bend.rst) sections.
It also includes a predefined [Circuit model](Circuit_Model.ipynb), so it can be easily simulated as part of the full device.

As with any component, we add it as a reference.
In this case, however, there's no need to manually specify the connections because the route is already created with the required translation (rotation, etc.) in place.

In [9]:
route1 = pf.parametric.route(port1=(spiral_ref, "P1"), port2=(coupler_ref2, "P1"))
component.add_reference(route1)
component

Note that the [spiral](../_autosummary/photonforge.parametric.rectangular_spiral.rst) parametric component does include an argument to provide a similar geometry (`align_ports="y"`), but using that would defeat the purpose of demonstrating the route generation.

The remaining connection between the 2 coupler references could be made in a similar fashion.
For the sake of demonstrating the flexibility of `route`, let's imagine that there's a region we need to avoid between the ports we want to connect.
We will add a rectangle here to indicate the obstacle that prevents a direct route:

In [10]:
component.add(
    "SLAB", pf.Rectangle(center=(spiral_ref.x_mid + 2.5, -7.5), size=(10, 15))
)

Using the `waypoints` argument in `route` we can specify a list of points that the route must cross (we can also specify the route direction at each point, if we so desire).
We use that feature here to go around the avoided region:

In [11]:
route2 = pf.parametric.route(
    port1=(coupler_ref1, "P2"),
    port2=(coupler_ref2, "P0"),
    waypoints=[(coupler_ref1.x_max + 10, -20), (coupler_ref2.x_min - 10, -20)],
)
component.add(route2)

We can get the path length from routes using the [route_length](../_autosummary/photonforge.route_length.rst) function.
Note that it also works for the rectangular spiral, because it is also built as a single continuous path.
Similarly, it can be used with [straight](../_autosummary/photonforge.parametric.straight.rst), [transition](../_autosummary/photonforge.parametric.transition.rst), [bend](../_autosummary/photonforge.parametric.bend.rst), [s_bend](../_autosummary/photonforge.parametric.s_bend.rst), combinations of those, or any component built with connected [paths](../_autosummary/photonforge.Path.rst).

In [12]:
print(f"Route 1 length: {pf.route_length(route1):.2f} μm")
print(f"Route 2 length: {pf.route_length(route2):.2f} μm")
print(f"Rectangular spiral length: {pf.route_length(spiral):.2f} μm")

Route 1 length: 42.20 μm
Route 2 length: 66.27 μm
Rectangular spiral length: 315.57 μm


### Other routing functions

Besides `route`, there are other parametric routing functions that can be used with [ports](Ports.ipynb) and [terminals](Electrical_Ports.ipynb).

- [route](../_autosummary/photonforge.parametric.route.rst)
- [route_s_bend](../_autosummary/photonforge.parametric.route_s_bend.rst)
- [route_taper](../_autosummary/photonforge.parametric.route_taper.rst)
- [route_manhattan](../_autosummary/photonforge.parametric.route_manhattan.rst)

The API reference documentation for each function includes short examples, while more complex use cases can be found in a few example notebooks, such as [Quantum Chip](../examples/Quantum_Chip.ipynb) and [EO-MZM](../examples/EO-MZM.ipynb).

### Updating routes

Because routes are parametric components, they can be updated easily when the references they are connecting are modified.
For example, let's move the second coupler reference.
The connections we created will no longer be valid.

In [13]:
coupler_ref2.translate((5, -15))
component

However, because they are parametric components, they store the keyword arguments they were created with, so that they can be easily [updated](Parametric_Component_Library.ipynb#Component-Updates).
In this case, we don't need to pass any new parameters to the component (although we definitely could), we just want the routes to be recalculated:

In [14]:
route1.update()
route2.update()
component

Besides directly connecting and building routes to connect ports, PhotonForge also offers the possibility of [defining virtual connections](../_autosummary/photonforge.Component.rst#photonforge.Component.add_virtual_connection), which can help setting up system-level simulations before the final layout and routing is in place.
More information about virtual connections can be found in the [Circuit Model](Circuit_Model.ipynb) guide.